# ctypes bitfield problem

I have some binary data, produced with C/C++. When using the code given below,
something seems to be a bit off. Probably I missed some flag or so.

An example of the data is:

```
bytes([67, 165, 195, 254, 255, 18, 0, 191, 0, 64])
```

# packing using C/C++

In [1]:
%%writefile test.cpp

#include <iostream>
#include <cstdint>

#define MSG_LEN 10

using namespace std;
union  measurement_msg {
        struct __attribute__((__packed__)) {
            uint16_t ts : 16;
            int32_t gyro_x : 20;
            int32_t gyro_y : 20;
            int32_t gyro_z : 20;
        } values;
        std::uint8_t raw[MSG_LEN];
};

int main()
{
    union  measurement_msg test;
    
    test.values.ts = 42307;
    test.values.gyro_x = -317;
    test.values.gyro_y = 303;
    test.values.gyro_z = 191;
    
    for (auto &val : test.raw) {
        cout << (int)val << ", ";
    }
    cout << endl;

    return 0;
}

Overwriting test.cpp


**WARNING: next file compiles and runs code on your computer**

In [2]:
!g++ test.cpp && ./a.out

67, 165, 195, 254, 255, 18, 0, 191, 0, 0, 


## ctypes unpacking

using `67 165 195 254 255 18 0 191 0 0`

In [3]:
from ctypes import *

MSG_LEN = 10

class Values(LittleEndianStructure):
    _pack_ = 1
    _fields_ = [
        ("ts", c_uint16, 16), 
        ("gyro_x", c_int32, 20),
        ("gyro_y", c_int32, 20),
        ("gyro_z", c_int32, 20)
    ]

class Data(Union):
    _fields_ = [("values", Values), ("raw", c_ubyte * MSG_LEN)]

In [4]:
example = Data()

#example.raw = bytes([67, 165, 195, 254, 255, 18, 0, 191, 0, 64])
example.raw = (c_ubyte*10)(67, 165, 195, 254, 255, 18, 0, 191, 0, 0)
example.values.ts, example.values.gyro_x, example.values.gyro_y, example.values.gyro_z

(42307, -317, 48896, 0)

result is off starting from `gyro_y` :(